In [1]:
%matplotlib inline

Within-subject SVM classification based on beta weights (per trials) averaged within networks from different grains of MIST parcellation, for CIMAQ memory encoding task (fMRI data).
Mean network betas reflect the engagement of a particular network for each trial.
MIST Parcellations include: 7, 12, 20, 36, 64, 122, 197, 325, 444 networks

Trials (conditions) are classifierd according to:
- task condition (encoding or control task)
- memory performance (hit vs miss, correct vs incorrect source)
- stimulus category (?)

Each model is ran and tested on data from the same subject, and then group statistics (confidence intervals) are computed around accuracy scores from each individual participant.

In [13]:
from pathlib import Path
sorted(Path('/data/simexp/datasets/cimaq_03-19/').rglob('*mist*'))

[]

In [2]:
import os
import sys
import glob
import numpy as np
import pandas as pd
import nilearn
import scipy
import nibabel as nb
import sklearn
import seaborn as sns
import itertools

from numpy import nan as NaN
from matplotlib import pyplot as plt
from nilearn import image, plotting
from nilearn import masking
from nilearn import plotting
from nilearn import datasets
from nilearn.plotting import plot_stat_map, plot_roi, plot_anat, plot_img, show
from nilearn.input_data import NiftiMasker, NiftiLabelsMasker
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC, LinearSVC
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix, precision_score, f1_score
from sklearn.model_selection import cross_val_predict, cross_val_score
from sklearn.preprocessing import MinMaxScaler


/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/datasets/__init__.py:96: FutureWarning: Fetchers from the nilearn.datasets module will be updated in version 0.9 to return python strings instead of bytes and Pandas dataframes instead of Numpy arrays.
  "Numpy arrays.", FutureWarning)


Step 1: import list of participants, and generate sublists of participants who have enough trials per category for each classification.

Encoding vs Control task conditions (all 94)
Stimulus category (all 94)
Hit versus Miss (42 participants; at least 15 trials per condition)
Correct Source versus Wrong Source (49 participants; at least 15 trials per condition)
Correct Source versus Miss (38 participants; at least 15 trials per condition)
*NOTE: ADD filter to exclude participants with too many scrubbed frames?? *

In [3]:

# Path to directory with participant lists
data_file = '/Users/mombot/Documents/Simexp/CIMAQ/Data/Participants/Splitting/Sub_list.tsv'
sub_data = pd.read_csv(data_file, sep = '\t')

# Exclude participants who failed QC
sub_data = sub_data[sub_data['QC_status']!= 'F']

## ADD filter to exclude participants with too many scrubbed frames?? ##

# Set minimal number of trials needed per subject to include them in analysis
num = 14

# Encoding vs Control, and Stimulus Category classifications
all_subs = sub_data['participant_id']
all_diagnosis = sub_data['cognitive_status']
print(all_subs)
print(len(all_subs))

# Hit versus Miss
hm_data = sub_data[sub_data['hits'] > num]
hm_data = hm_data[hm_data['miss'] > num]
hm_subs = hm_data['participant_id']
hm_diagnosis = hm_data['cognitive_status']
print(hm_subs)
print(len(hm_subs))

# Correct Source versus Wrong Source 
cw_data = sub_data[sub_data['correct_source'] > num]
cw_data = cw_data[cw_data['wrong_source'] > num]
cw_subs = cw_data['participant_id']
cw_diagnosis = cw_data['cognitive_status']
print(cw_subs)
print(len(cw_subs))

# Correct Source versus Miss
cmiss_data = sub_data[sub_data['correct_source'] > num]
cmiss_data = cmiss_data[cmiss_data['miss'] > num]
cmiss_subs = cmiss_data['participant_id']
cmiss_diagnosis = cmiss_data['cognitive_status']
print(cmiss_subs)
print(len(cmiss_subs))


FileNotFoundError: [Errno 2] No such file or directory: '/Users/mombot/Documents/Simexp/CIMAQ/Data/Participants/Splitting/Sub_list.tsv'

Step 2. Set up paths of directories of interest

Create empty data structures to save and export classification results


In [6]:
# set paths to directories of interest
beta_dir = '/Users/mombot/Documents/Simexp/CIMAQ/Data/Nistats/Betas'
label_dir = '/Users/mombot/Documents/Simexp/CIMAQ/Data/Nistats/Events'
mask_dir = '/Users/mombot/Documents/Simexp/CIMAQ/Data/masks'
output_dir = '/Users/mombot/Documents/Simexp/CIMAQ/Data/Nilearn/Group_results'
basc_dir = '/Users/mombot/Documents/Simexp/CIMAQ/Data/MIST/Release/Parcellations'

# set the parcellation level and load the parcellation map
# 7, 12, 20, 36, 64, 122, 197, 325, 444
numnets = [7, 20, 64, 325, 444]


Step 3. ENCODING VERSUS CONTROL TASK CLASSIFICATION

Build and test model for each participant on list, and compile data in a single pandas dataframe

In [7]:
# ENCODING VERSUS CONTROL TASK CLASSIFICATION

for numnet in numnets:

    basc = image.load_img(os.path.join(basc_dir, 'MIST_'+str(numnet)+'.nii'))
    b_labels = '/Users/mombot/Documents/Simexp/CIMAQ/Data/MIST/Release/Parcel_Information/MIST_'+str(numnet)+'.csv'
    basc_labels = pd.read_csv(b_labels, sep=';')

    # build data structure to store accuracy data and coefficients
    enc_ctl_data = pd.DataFrame()
    enc_ctl_data.insert(loc = 0, column = 'dccid', value = 'None', allow_duplicates=True)
    for i in range(0, 10):
        enc_ctl_data.insert(loc = enc_ctl_data.shape[1], column = 'CV'+str(i+1)+'_acc',
                            value = NaN, allow_duplicates=True)
        enc_ctl_data.insert(loc = enc_ctl_data.shape[1], column = 'TrainSet_MeanCV_acc',
                            value = 'None', allow_duplicates=True)
        enc_ctl_data.insert(loc = enc_ctl_data.shape[1], column = 'TestSet_acc',
                            value = 'None', allow_duplicates=True)
        netnames = basc_labels['name']
    for i in range(0, numnet):
        enc_ctl_data.insert(loc = enc_ctl_data.shape[1], column = netnames[i]+'_coef',
                            value = NaN, allow_duplicates=True)

    for sub in all_subs:
        print(sub)
        s_data = [sub]
        # load subject's beta maps (one per trial)
        betas = image.load_img(img=os.path.join(beta_dir, str(sub),
                                                f'TrialContrasts/betas_{session.sub_id}*.nii'),
                               wildcards=True)
        # initialize NiftiLabelMasker object    
        sub_mask = nb.load(os.path.join(mask_dir, 'func_sub'+str(sub)+'_mask_stereonl.nii'))
        sub_label_masker = NiftiLabelsMasker(labels_img=basc, standardize=True, mask_img=sub_mask,
                                             memory = 'nilearn_cache', verbose=0)

        # transform subject's beta maps into vector of network means per trial
        X_enc_ctl = sub_label_masker.fit_transform(betas)

        # load subject's trial labels
        labels_file = os.path.join(label_dir, 'sub-'+str(sub)+'_enco_ctl.tsv')
        enco_ctl_labels = pd.read_csv(labels_file, sep='\t')
        y_enco_ctl = enco_ctl_labels['condition']

        # mask data to exclude trials of no interest
        # does not apply here

        # Split trials into a training and a test set
        X_train, X_test, y_train, y_test = train_test_split(
            X_enc_ctl, # x
            y_enco_ctl, # y
            test_size = 0.4, # 60%/40% split
            shuffle = True, # shuffle dataset before splitting
            stratify = y_enco_ctl, # keep distribution of conditions consistent betw. train & test sets
            #random_state = 123  # if set number, same shuffle each time, otherwise randomization algo
            ) 
        print('training:', len(X_train), 'testing:', len(X_test))
        print(y_train.value_counts(), y_test.value_counts())

        # define the model
        sub_svc = SVC(kernel='linear', class_weight='balanced')

        # do cross-validation to evaluate model performance
        # within 10 folds of training set
        # predict
        y_pred = cross_val_predict(sub_svc, X_train, y_train,
                                   groups=y_train, cv=10)
        # scores
        cv_acc = cross_val_score(sub_svc, X_train, y_train,
                             groups=y_train, cv=10)
        print(cv_acc)

        for i in range(0, len(cv_acc)):
            s_data.append(cv_acc[i])

        # evaluate overall model performance on training data
        overall_acc = accuracy_score(y_pred = y_pred, y_true = y_train)
        overall_cr = classification_report(y_pred = y_pred, y_true = y_train)
        print('Accuracy:',overall_acc)
        print(overall_cr)

        s_data.append(overall_acc)

        # Test model on unseen data from the test set
        sub_svc.fit(X_train, y_train)
        y_pred = sub_svc.predict(X_test) # classify age class using testing data
        acc = sub_svc.score(X_test, y_test) # get accuracy

        cr = classification_report(y_pred=y_pred, y_true=y_test) # get prec., recall & f1
        # print results
        print('accuracy =', acc)
        print(cr)  

        s_data.append(acc)

        # get coefficients
        coef_ = sub_svc.coef_[0]
        print(coef_.shape)
        print(coef_)

        sub_basc = basc_labels.copy()
        sub_basc.insert(loc=3, column='coef', value=coef_, allow_duplicates=True)

        coef = sub_basc['coef']
        for j in range(0, len(coef)):
            s_data.append(coef[j])

        #sub_basc.sort_values(by='coef', axis = 0, ascending = False, inplace=True)
        #print(sub_basc.iloc[0:12, 2:4])

        enc_ctl_data = enc_ctl_data.append(pd.Series(s_data, index=enc_ctl_data.columns), ignore_index=True)


    demo_data = sub_data.copy()
    demo_data.reset_index(level=None, drop=False, inplace=True)

    enc_ctl_data.insert(loc = 1, column = 'cognitive_status',
                        value = demo_data['cognitive_status'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 2, column = 'total_scrubbed_frames',
                        value = demo_data['total_scrubbed_frames'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 3, column = 'mean_FD',
                        value = demo_data['mean_FD'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 4, column = 'hits', value = demo_data['hits'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 5, column = 'miss', value = demo_data['miss'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 6, column = 'correct_source',
                        value = demo_data['correct_source'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 7, column = 'wrong_source',
                        value = demo_data['wrong_source'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 8, column = 'dprime',
                        value = demo_data['dprime'], allow_duplicates=True)
    enc_ctl_data.insert(loc = 9, column = 'associative_memScore',
                        value = demo_data['associative_memScore'], allow_duplicates=True)    

    enc_ctl_data.to_csv(os.path.join(output_dir, 'SVC_withinSub_enc_ctl_'+str(numnet)+'networks.tsv'),
        sep='\t', header=True, index=False)


108391
training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.5        0.625      0.875      0.71428571 0.71428571 0.57142857
 0.71428571 0.33333333 0.5        0.66666667]
Accuracy: 0.6285714285714286
              precision    recall  f1-score   support

         CTL       0.45      0.61      0.52        23
         Enc       0.77      0.64      0.70        47

   micro avg       0.63      0.63      0.63        70
   macro avg       0.61      0.62      0.61        70
weighted avg       0.66      0.63      0.64        70

accuracy = 0.5106382978723404
              precision    recall  f1-score   support

         CTL       0.33      0.44      0.38        16
         Enc       0.65      0.55      0.60        31

   micro avg       0.51      0.51      0.51        47
   macro avg       0.49      0.49      0.49        47
weighted avg       0.54      0.51      0.52        47

(7,)
[-0.63574298  0.71036072  0.08931085 

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.625      0.25       0.875      0.71428571 0.85714286 0.85714286
 0.71428571 0.66666667 0.83333333 0.83333333]
Accuracy: 0.7142857142857143
              precision    recall  f1-score   support

         CTL       0.55      0.74      0.63        23
         Enc       0.85      0.70      0.77        47

   micro avg       0.71      0.71      0.71        70
   macro avg       0.70      0.72      0.70        70
weighted avg       0.75      0.71      0.72        70

accuracy = 0.7021276595744681
              precision    recall  f1-score   support

         CTL       0.55      0.69      0.61        16
         Enc       0.81      0.71      0.76        31

   micro avg       0.70      0.70      0.70        47
   macro avg       0.68      0.70      0.68        47
weighted avg       0.72      0.70      0.71        47

(7,)
[0.07731822 0.47991269 0.81544146 1.41757079

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.75       0.625      0.625      1.         0.71428571 0.57142857
 0.57142857 1.         0.66666667 0.66666667]
Accuracy: 0.7142857142857143
              precision    recall  f1-score   support

         CTL       0.57      0.57      0.57        23
         Enc       0.79      0.79      0.79        47

   micro avg       0.71      0.71      0.71        70
   macro avg       0.68      0.68      0.68        70
weighted avg       0.71      0.71      0.71        70

accuracy = 0.6808510638297872
              precision    recall  f1-score   support

         CTL       0.54      0.44      0.48        16
         Enc       0.74      0.81      0.77        31

   micro avg       0.68      0.68      0.68        47
   macro avg       0.64      0.62      0.63        47
weighted avg       0.67      0.68      0.67        47

(7,)
[-0.34682802 -0.61223288 -0.09357178  0.1636

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.5        0.625      0.5        0.42857143 0.28571429 0.71428571
 0.71428571 0.83333333 0.5        0.66666667]
Accuracy: 0.5714285714285714
              precision    recall  f1-score   support

         CTL       0.39      0.57      0.46        23
         Enc       0.73      0.57      0.64        47

   micro avg       0.57      0.57      0.57        70
   macro avg       0.56      0.57      0.55        70
weighted avg       0.62      0.57      0.58        70

accuracy = 0.6170212765957447
              precision    recall  f1-score   support

         CTL       0.45      0.62      0.53        16
         Enc       0.76      0.61      0.68        31

   micro avg       0.62      0.62      0.62        47
   macro avg       0.61      0.62      0.60        47
weighted avg       0.66      0.62      0.63        47

(7,)
[ 0.11287769 -0.44235937 -0.09649321  0.7674

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.375      0.375      0.625      0.42857143 0.28571429 0.42857143
 0.14285714 0.5        0.16666667 0.33333333]
Accuracy: 0.37142857142857144
              precision    recall  f1-score   support

         CTL       0.27      0.52      0.35        23
         Enc       0.56      0.30      0.39        47

   micro avg       0.37      0.37      0.37        70
   macro avg       0.41      0.41      0.37        70
weighted avg       0.46      0.37      0.38        70

accuracy = 0.7021276595744681
              precision    recall  f1-score   support

         CTL       0.54      0.81      0.65        16
         Enc       0.87      0.65      0.74        31

   micro avg       0.70      0.70      0.70        47
   macro avg       0.71      0.73      0.70        47
weighted avg       0.76      0.70      0.71        47

(7,)
[ 0.55005431  0.17343704  0.1858714   0.083

...

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[1.         1.         0.875      0.71428571 1.         0.71428571
 0.85714286 0.83333333 1.         0.83333333]
Accuracy: 0.8857142857142857
              precision    recall  f1-score   support

         CTL       0.83      0.83      0.83        23
         Enc       0.91      0.91      0.91        47

   micro avg       0.89      0.89      0.89        70
   macro avg       0.87      0.87      0.87        70
weighted avg       0.89      0.89      0.89        70

accuracy = 0.7872340425531915
              precision    recall  f1-score   support

         CTL       0.75      0.56      0.64        16
         Enc       0.80      0.90      0.85        31

   micro avg       0.79      0.79      0.79        47
   macro avg       0.78      0.73      0.75        47
weighted avg       0.78      0.79      0.78        47

(444,)
[-1.22001135e-02  7.66069749e-03  2.785387

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.625      0.75       0.875      0.85714286 0.71428571 0.71428571
 0.85714286 0.83333333 0.83333333 0.66666667]
Accuracy: 0.7714285714285715
              precision    recall  f1-score   support

         CTL       0.67      0.61      0.64        23
         Enc       0.82      0.85      0.83        47

   micro avg       0.77      0.77      0.77        70
   macro avg       0.74      0.73      0.73        70
weighted avg       0.77      0.77      0.77        70

accuracy = 0.7659574468085106
              precision    recall  f1-score   support

         CTL       0.67      0.62      0.65        16
         Enc       0.81      0.84      0.83        31

   micro avg       0.77      0.77      0.77        47
   macro avg       0.74      0.73      0.74        47
weighted avg       0.76      0.77      0.76        47

(444,)
[ 0.01912503  0.01671241  0.00899667 -0.02

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.75       1.         1.         0.85714286 0.85714286 1.
 1.         0.66666667 0.33333333 0.83333333]
Accuracy: 0.8428571428571429
              precision    recall  f1-score   support

         CTL       0.80      0.70      0.74        23
         Enc       0.86      0.91      0.89        47

   micro avg       0.84      0.84      0.84        70
   macro avg       0.83      0.81      0.82        70
weighted avg       0.84      0.84      0.84        70

accuracy = 0.7659574468085106
              precision    recall  f1-score   support

         CTL       0.73      0.50      0.59        16
         Enc       0.78      0.90      0.84        31

   micro avg       0.77      0.77      0.77        47
   macro avg       0.75      0.70      0.71        47
weighted avg       0.76      0.77      0.75        47

(444,)
[ 3.15346785e-02 -4.43796388e-03 -3.33676494e-02  

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.875      0.875      0.875      0.71428571 1.         1.
 1.         0.66666667 1.         0.83333333]
Accuracy: 0.8857142857142857
              precision    recall  f1-score   support

         CTL       0.76      0.96      0.85        23
         Enc       0.98      0.85      0.91        47

   micro avg       0.89      0.89      0.89        70
   macro avg       0.87      0.90      0.88        70
weighted avg       0.90      0.89      0.89        70

accuracy = 0.8297872340425532
              precision    recall  f1-score   support

         CTL       0.90      0.56      0.69        16
         Enc       0.81      0.97      0.88        31

   micro avg       0.83      0.83      0.83        47
   macro avg       0.86      0.77      0.79        47
weighted avg       0.84      0.83      0.82        47

(444,)
[ 1.19839882e-05 -1.35808081e-02 -1.55508887e-02  

training: 70 testing: 47
Enc    47
CTL    23
Name: condition, dtype: int64 Enc    31
CTL    16
Name: condition, dtype: int64
[0.75       0.5        0.875      1.         0.42857143 0.71428571
 0.71428571 0.66666667 0.83333333 0.83333333]
Accuracy: 0.7285714285714285
              precision    recall  f1-score   support

         CTL       0.58      0.61      0.60        23
         Enc       0.80      0.79      0.80        47

   micro avg       0.73      0.73      0.73        70
   macro avg       0.69      0.70      0.70        70
weighted avg       0.73      0.73      0.73        70

accuracy = 0.9148936170212766
              precision    recall  f1-score   support

         CTL       0.88      0.88      0.88        16
         Enc       0.94      0.94      0.94        31

   micro avg       0.91      0.91      0.91        47
   macro avg       0.91      0.91      0.91        47
weighted avg       0.91      0.91      0.91        47

(444,)
[-1.19811885e-02  8.09809577e-03 -1.890478

In [9]:
# HIT VERSUS MISS TRIAL CLASSIFICATION
for numnet in numnets:

    basc = image.load_img(os.path.join(basc_dir, 'MIST_'+str(numnet)+'.nii'))
    b_labels = '/Users/mombot/Documents/Simexp/CIMAQ/Data/MIST/Release/Parcel_Information/MIST_'+str(numnet)+'.csv'
    basc_labels = pd.read_csv(b_labels, sep=';')
    
    # build data structure to store accuracy data and coefficients
    hit_miss_data = pd.DataFrame()
    hit_miss_data.insert(loc = 0, column = 'dccid', value = 'None', allow_duplicates=True)
    # hit_miss_data.insert(loc = 1, column = 'diagnosis', value = 'None', allow_duplicates=True)
    for i in range(0, 7):
        hit_miss_data.insert(loc = hit_miss_data.shape[1], column = 'CV'+str(i+1)+'_acc', value = NaN, allow_duplicates=True)
    hit_miss_data.insert(loc = hit_miss_data.shape[1], column = 'TrainSet_MeanCV_acc', value = 'None', allow_duplicates=True)
    hit_miss_data.insert(loc = hit_miss_data.shape[1], column = 'TestSet_acc', value = 'None', allow_duplicates=True)
    netnames = basc_labels['name']
    for i in range(0, numnet):
        hit_miss_data.insert(loc = hit_miss_data.shape[1], column = netnames[i]+'_coef', value = NaN, allow_duplicates=True)

    for sub in hm_subs:
        print(sub)
        s_data = [sub]
        # load subject's beta maps (one per trial)
        betas = image.load_img(img=os.path.join(beta_dir, str(sub), 'TrialContrasts/betas_sub'+str(sub)+'*.nii'),
                               wildcards=True)
        # initialize NiftiLabelMasker object    
        sub_mask = nb.load(os.path.join(mask_dir, 'func_sub'+str(sub)+'_mask_stereonl.nii'))
        sub_label_masker = NiftiLabelsMasker(labels_img=basc, standardize=True, mask_img=sub_mask,
                                             memory = 'nilearn_cache', verbose=0)

        # transform subject's beta maps into vector of network means per trial
        X_hit_miss_ctl = sub_label_masker.fit_transform(betas)   

        # load subject's trial labels
        labels_file = os.path.join(label_dir, 'sub-'+str(sub)+'_ctl_miss_hit.tsv')
        y_hit_miss_ctl = pd.read_csv(labels_file, sep='\t')
        y_hit_miss_ctl_labels = y_hit_miss_ctl['ctl_miss_hit']
        # mask X and y data to exclude trials of no interest
        hit_miss_mask = y_hit_miss_ctl_labels.isin(['hit', 'missed'])
        y_hit_miss = y_hit_miss_ctl_labels[hit_miss_mask]      
        X_hit_miss  = X_hit_miss_ctl[hit_miss_mask]

        # Split trials into a training and a test set
        X_train, X_test, y_train, y_test = train_test_split(
            X_hit_miss, # x
            y_hit_miss, # y
            test_size = 0.4, # 60%/40% split
            shuffle = True, # shuffle dataset before splitting
            stratify = y_hit_miss, # keep distribution of conditions consistent betw. train & test sets
            #random_state = 123  # if set number, same shuffle each time, otherwise randomization algo
            ) 
        print('training:', len(X_train), 'testing:', len(X_test))
        print(y_train.value_counts(), y_test.value_counts())

        # define the model
        sub_svc = SVC(kernel='linear', class_weight='balanced')

        # do cross-validation to evaluate model performance
        # within 10 folds of training set
        # predict
        y_pred = cross_val_predict(sub_svc, X_train, y_train,
                                   groups=y_train, cv=7)
        # scores
        cv_acc = cross_val_score(sub_svc, X_train, y_train,
                             groups=y_train, cv=7)
        print(cv_acc)

        for i in range(0, len(cv_acc)):
            s_data.append(cv_acc[i])

        # evaluate overall model performance on training data
        overall_acc = accuracy_score(y_pred = y_pred, y_true = y_train)
        overall_cr = classification_report(y_pred = y_pred, y_true = y_train)
        print('Accuracy:',overall_acc)
        print(overall_cr)

        s_data.append(overall_acc)

        # Test model on unseen data from the test set
        sub_svc.fit(X_train, y_train)
        y_pred = sub_svc.predict(X_test) # classify age class using testing data
        acc = sub_svc.score(X_test, y_test) # get accuracy

        cr = classification_report(y_pred=y_pred, y_true=y_test) # get prec., recall & f1
        # print results
        print('accuracy =', acc)
        print(cr)  

        s_data.append(acc)

        # get coefficients
        coef_ = sub_svc.coef_[0]
        print(coef_.shape)
        print(coef_)

        sub_basc = basc_labels.copy()
        sub_basc.insert(loc=3, column='coef', value=coef_, allow_duplicates=True)

        coef = sub_basc['coef']
        for j in range(0, len(coef)):
            s_data.append(coef[j])

        #sub_basc.sort_values(by='coef', axis = 0, ascending = False, inplace=True)
        #print(sub_basc.iloc[0:12, 2:4])

        hit_miss_data = hit_miss_data.append(pd.Series(s_data, index=hit_miss_data.columns), ignore_index=True)

    demo_data = hm_data.copy()
    demo_data.reset_index(level=None, drop=False, inplace=True)

    hit_miss_data.insert(loc = 1, column = 'cognitive_status', value = demo_data['cognitive_status'], allow_duplicates=True)
    hit_miss_data.insert(loc = 2, column = 'total_scrubbed_frames', value = demo_data['total_scrubbed_frames'], allow_duplicates=True)
    hit_miss_data.insert(loc = 3, column = 'mean_FD', value = demo_data['mean_FD'], allow_duplicates=True)
    hit_miss_data.insert(loc = 4, column = 'hits', value = demo_data['hits'], allow_duplicates=True)
    hit_miss_data.insert(loc = 5, column = 'miss', value = demo_data['miss'], allow_duplicates=True)
    hit_miss_data.insert(loc = 6, column = 'correct_source', value = demo_data['correct_source'], allow_duplicates=True)
    hit_miss_data.insert(loc = 7, column = 'wrong_source', value = demo_data['wrong_source'], allow_duplicates=True)
    hit_miss_data.insert(loc = 8, column = 'dprime', value = demo_data['dprime'], allow_duplicates=True)
    hit_miss_data.insert(loc = 9, column = 'associative_memScore', value = demo_data['associative_memScore'], allow_duplicates=True)    

    hit_miss_data.to_csv(os.path.join(output_dir, 'SVC_withinSub_hit_miss_'+str(numnet)+'networks.tsv'),
        sep='\t', header=True, index=False)


108391
training: 46 testing: 32
hit       37
missed     9
Name: ctl_miss_hit, dtype: int64 hit       26
missed     6
Name: ctl_miss_hit, dtype: int64
[0.375      0.25       0.5        0.16666667 0.83333333 0.33333333
 0.66666667]
Accuracy: 0.43478260869565216
              precision    recall  f1-score   support

         hit       0.72      0.49      0.58        37
      missed       0.10      0.22      0.13         9

   micro avg       0.43      0.43      0.43        46
   macro avg       0.41      0.35      0.36        46
weighted avg       0.60      0.43      0.49        46

accuracy = 0.5
              precision    recall  f1-score   support

         hit       0.86      0.46      0.60        26
      missed       0.22      0.67      0.33         6

   micro avg       0.50      0.50      0.50        32
   macro avg       0.54      0.56      0.47        32
weighted avg       0.74      0.50      0.55        32

(7,)
[ 0.42976251  0.52415022 -0.13950035 -0.52690363 -0.08410008  0.06

/anaconda3/envs/may19_py36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


training: 46 testing: 32
hit       30
missed    16
Name: ctl_miss_hit, dtype: int64 hit       21
missed    11
Name: ctl_miss_hit, dtype: int64
[0.625 0.75  0.5   0.5   0.5   0.5   1.   ]
Accuracy: 0.6304347826086957
              precision    recall  f1-score   support

         hit       0.78      0.60      0.68        30
      missed       0.48      0.69      0.56        16

   micro avg       0.63      0.63      0.63        46
   macro avg       0.63      0.64      0.62        46
weighted avg       0.68      0.63      0.64        46

accuracy = 0.5
              precision    recall  f1-score   support

         hit       0.65      0.52      0.58        21
      missed       0.33      0.45      0.38        11

   micro avg       0.50      0.50      0.50        32
   macro avg       0.49      0.49      0.48        32
weighted avg       0.54      0.50      0.51        32

(7,)
[-0.37911983 -0.828222   -0.07358854  0.39878489  0.26632836 -0.14416811
  0.56272883]
258912
training: 44 tes

training: 46 testing: 32
hit       34
missed    12
Name: ctl_miss_hit, dtype: int64 hit       24
missed     8
Name: ctl_miss_hit, dtype: int64
[0.85714286 0.71428571 0.42857143 0.28571429 0.71428571 0.33333333
 0.8       ]
Accuracy: 0.5869565217391305
              precision    recall  f1-score   support

         hit       0.80      0.59      0.68        34
      missed       0.33      0.58      0.42        12

   micro avg       0.59      0.59      0.59        46
   macro avg       0.57      0.59      0.55        46
weighted avg       0.68      0.59      0.61        46

accuracy = 0.625
              precision    recall  f1-score   support

         hit       0.83      0.62      0.71        24
      missed       0.36      0.62      0.45         8

   micro avg       0.62      0.62      0.62        32
   macro avg       0.60      0.62      0.58        32
weighted avg       0.71      0.62      0.65        32

(7,)
[ 0.40378     0.24744028  0.59493091  0.64498656  0.80198372  0.25744821

training: 46 testing: 32
hit       25
missed    21
Name: ctl_miss_hit, dtype: int64 hit       17
missed    15
Name: ctl_miss_hit, dtype: int64
[0.85714286 0.42857143 0.57142857 0.42857143 0.16666667 0.66666667
 0.5       ]
Accuracy: 0.5217391304347826
              precision    recall  f1-score   support

         hit       0.57      0.52      0.54        25
      missed       0.48      0.52      0.50        21

   micro avg       0.52      0.52      0.52        46
   macro avg       0.52      0.52      0.52        46
weighted avg       0.53      0.52      0.52        46

accuracy = 0.46875
              precision    recall  f1-score   support

         hit       0.50      0.59      0.54        17
      missed       0.42      0.33      0.37        15

   micro avg       0.47      0.47      0.47        32
   macro avg       0.46      0.46      0.46        32
weighted avg       0.46      0.47      0.46        32

(7,)
[ 0.67738949 -0.02713414  0.79756428 -0.28854452  0.53687825  0.150439

...

training: 46 testing: 32
hit       36
missed    10
Name: ctl_miss_hit, dtype: int64 hit       25
missed     7
Name: ctl_miss_hit, dtype: int64
[0.625      0.57142857 0.57142857 0.83333333 0.83333333 0.66666667
 0.66666667]
Accuracy: 0.6739130434782609
              precision    recall  f1-score   support

         hit       0.80      0.78      0.79        36
      missed       0.27      0.30      0.29        10

   micro avg       0.67      0.67      0.67        46
   macro avg       0.54      0.54      0.54        46
weighted avg       0.69      0.67      0.68        46

accuracy = 0.65625
              precision    recall  f1-score   support

         hit       0.79      0.76      0.78        25
      missed       0.25      0.29      0.27         7

   micro avg       0.66      0.66      0.66        32
   macro avg       0.52      0.52      0.52        32
weighted avg       0.67      0.66      0.66        32

(444,)
[-0.005099   -0.01579771 -0.01938239 -0.01542398 -0.00637419 -0.0032

training: 46 testing: 32
hit       34
missed    12
Name: ctl_miss_hit, dtype: int64 hit       24
missed     8
Name: ctl_miss_hit, dtype: int64
[0.57142857 0.71428571 0.71428571 0.42857143 0.85714286 0.83333333
 0.8       ]
Accuracy: 0.6956521739130435
              precision    recall  f1-score   support

         hit       0.76      0.85      0.81        34
      missed       0.38      0.25      0.30        12

   micro avg       0.70      0.70      0.70        46
   macro avg       0.57      0.55      0.55        46
weighted avg       0.66      0.70      0.67        46

accuracy = 0.6875
              precision    recall  f1-score   support

         hit       0.79      0.79      0.79        24
      missed       0.38      0.38      0.38         8

   micro avg       0.69      0.69      0.69        32
   macro avg       0.58      0.58      0.58        32
weighted avg       0.69      0.69      0.69        32

(444,)
[-5.33019899e-03  4.18524338e-02 -6.47847791e-03  9.12317463e-03
 -4.

training: 45 testing: 31
hit       27
missed    18
Name: ctl_miss_hit, dtype: int64 hit       19
missed    12
Name: ctl_miss_hit, dtype: int64
[0.42857143 0.57142857 0.14285714 0.42857143 0.16666667 0.33333333
 0.2       ]
Accuracy: 0.3333333333333333
              precision    recall  f1-score   support

         hit       0.42      0.30      0.35        27
      missed       0.27      0.39      0.32        18

   micro avg       0.33      0.33      0.33        45
   macro avg       0.35      0.34      0.33        45
weighted avg       0.36      0.33      0.34        45

accuracy = 0.5483870967741935
              precision    recall  f1-score   support

         hit       0.69      0.47      0.56        19
      missed       0.44      0.67      0.53        12

   micro avg       0.55      0.55      0.55        31
   macro avg       0.57      0.57      0.55        31
weighted avg       0.60      0.55      0.55        31

(444,)
[ 6.59423003e-03  1.73998016e-02 -6.16700173e-03 -2.35297

training: 46 testing: 32
missed    27
hit       19
Name: ctl_miss_hit, dtype: int64 missed    19
hit       13
Name: ctl_miss_hit, dtype: int64
[0.71428571 0.85714286 0.42857143 0.57142857 0.57142857 0.66666667
 0.6       ]
Accuracy: 0.6304347826086957
              precision    recall  f1-score   support

         hit       0.56      0.53      0.54        19
      missed       0.68      0.70      0.69        27

   micro avg       0.63      0.63      0.63        46
   macro avg       0.62      0.62      0.62        46
weighted avg       0.63      0.63      0.63        46

accuracy = 0.625
              precision    recall  f1-score   support

         hit       0.54      0.54      0.54        13
      missed       0.68      0.68      0.68        19

   micro avg       0.62      0.62      0.62        32
   macro avg       0.61      0.61      0.61        32
weighted avg       0.62      0.62      0.62        32

(444,)
[ 2.55763813e-02  7.11802091e-03 -2.79804741e-02  4.01712932e-02
 -5.2

training: 44 testing: 30
hit       27
missed    17
Name: ctl_miss_hit, dtype: int64 hit       19
missed    11
Name: ctl_miss_hit, dtype: int64
[0.57142857 0.57142857 0.28571429 0.83333333 0.33333333 0.33333333
 0.6       ]
Accuracy: 0.5
              precision    recall  f1-score   support

         hit       0.59      0.63      0.61        27
      missed       0.33      0.29      0.31        17

   micro avg       0.50      0.50      0.50        44
   macro avg       0.46      0.46      0.46        44
weighted avg       0.49      0.50      0.49        44

accuracy = 0.5333333333333333
              precision    recall  f1-score   support

         hit       0.63      0.63      0.63        19
      missed       0.36      0.36      0.36        11

   micro avg       0.53      0.53      0.53        30
   macro avg       0.50      0.50      0.50        30
weighted avg       0.53      0.53      0.53        30

(444,)
[ 1.57150169e-02 -1.17996655e-02 -1.53175039e-02  8.51933313e-02
  5.146

In [10]:
# CORRECT SOURCE VERSUS WRONG SOURCE TRIAL CLASSIFICATION

for numnet in numnets:

    basc = image.load_img(os.path.join(basc_dir, 'MIST_'+str(numnet)+'.nii'))
    b_labels = '/Users/mombot/Documents/Simexp/CIMAQ/Data/MIST/Release/Parcel_Information/MIST_'+str(numnet)+'.csv'
    basc_labels = pd.read_csv(b_labels, sep=';')

    # build data structure to store accuracy data and coefficients
    cs_ws_data = pd.DataFrame()
    cs_ws_data.insert(loc = 0, column = 'dccid', value = 'None', allow_duplicates=True)
    # cs_ws_data.insert(loc = 1, column = 'diagnosis', value = 'None', allow_duplicates=True)
    for i in range(0, 7):
        cs_ws_data.insert(loc = cs_ws_data.shape[1], column = 'CV'+str(i+1)+'_acc', value = NaN, allow_duplicates=True)
    cs_ws_data.insert(loc = cs_ws_data.shape[1], column = 'TrainSet_MeanCV_acc', value = 'None', allow_duplicates=True)
    cs_ws_data.insert(loc = cs_ws_data.shape[1], column = 'TestSet_acc', value = 'None', allow_duplicates=True)
    netnames = basc_labels['name']
    for i in range(0, numnet):
        cs_ws_data.insert(loc = cs_ws_data.shape[1], column = netnames[i]+'_coef', value = NaN, allow_duplicates=True)

    for sub in cw_subs:
        print(sub)
        s_data = [sub]
        # load subject's beta maps (one per trial)
        betas = image.load_img(img=os.path.join(beta_dir, str(sub), 'TrialContrasts/betas_sub'+str(sub)+'*.nii'),
                               wildcards=True)
        # initialize NiftiLabelMasker object    
        sub_mask = nb.load(os.path.join(mask_dir, 'func_sub'+str(sub)+'_mask_stereonl.nii'))
        sub_label_masker = NiftiLabelsMasker(labels_img=basc, standardize=True, mask_img=sub_mask,
                                             memory = 'nilearn_cache', verbose=0)

        # transform subject's beta maps into vector of network means per trial
        X_cs_ws_miss_ctl = sub_label_masker.fit_transform(betas)   

        # load subject's trial labels
        labels_file = os.path.join(label_dir, 'sub-'+str(sub)+'_ctl_miss_ws_cs.tsv')
        y_cs_ws_miss_ctl = pd.read_csv(labels_file, sep='\t')
        y_cs_ws_miss_ctl_labels = y_cs_ws_miss_ctl['ctl_miss_ws_cs']
        # mask X and y data to exclude trials of no interest
        cs_ws_mask = y_cs_ws_miss_ctl_labels.isin(['correctsource', 'wrongsource'])
        y_cs_ws = y_cs_ws_miss_ctl_labels[cs_ws_mask]      
        X_cs_ws  = X_cs_ws_miss_ctl[cs_ws_mask]

        # Split trials into a training and a test set
        X_train, X_test, y_train, y_test = train_test_split(
            X_cs_ws, # x
            y_cs_ws, # y
            test_size = 0.4, # 60%/40% split
            shuffle = True, # shuffle dataset before splitting
            stratify = y_cs_ws, # keep distribution of conditions consistent betw. train & test sets
            #random_state = 123  # if set number, same shuffle each time, otherwise randomization algo
            ) 
        print('training:', len(X_train), 'testing:', len(X_test))
        print(y_train.value_counts(), y_test.value_counts())

        # define the model
        sub_svc = SVC(kernel='linear', class_weight='balanced')

        # do cross-validation to evaluate model performance
        # within 10 folds of training set
        # predict
        y_pred = cross_val_predict(sub_svc, X_train, y_train,
                                   groups=y_train, cv=7)
        # scores
        cv_acc = cross_val_score(sub_svc, X_train, y_train,
                             groups=y_train, cv=7)
        print(cv_acc)

        for i in range(0, len(cv_acc)):
            s_data.append(cv_acc[i])

        # evaluate overall model performance on training data
        overall_acc = accuracy_score(y_pred = y_pred, y_true = y_train)
        overall_cr = classification_report(y_pred = y_pred, y_true = y_train)
        print('Accuracy:',overall_acc)
        print(overall_cr)

        s_data.append(overall_acc)

        # Test model on unseen data from the test set
        sub_svc.fit(X_train, y_train)
        y_pred = sub_svc.predict(X_test) # classify age class using testing data
        acc = sub_svc.score(X_test, y_test) # get accuracy

        cr = classification_report(y_pred=y_pred, y_true=y_test) # get prec., recall & f1
        # print results
        print('accuracy =', acc)
        print(cr)  

        s_data.append(acc)

        # get coefficients
        coef_ = sub_svc.coef_[0]
        print(coef_.shape)
        print(coef_)

        sub_basc = basc_labels.copy()
        sub_basc.insert(loc=3, column='coef', value=coef_, allow_duplicates=True)

        coef = sub_basc['coef']
        for j in range(0, len(coef)):
            s_data.append(coef[j])

        #sub_basc.sort_values(by='coef', axis = 0, ascending = False, inplace=True)
        #print(sub_basc.iloc[0:12, 2:4])

        cs_ws_data = cs_ws_data.append(pd.Series(s_data, index=cs_ws_data.columns), ignore_index=True)

    demo_data = cw_data.copy()
    demo_data.reset_index(level=None, drop=False, inplace=True)

    cs_ws_data.insert(loc = 1, column = 'cognitive_status', value = demo_data['cognitive_status'], allow_duplicates=True)
    cs_ws_data.insert(loc = 2, column = 'total_scrubbed_frames', value = demo_data['total_scrubbed_frames'], allow_duplicates=True)
    cs_ws_data.insert(loc = 3, column = 'mean_FD', value = demo_data['mean_FD'], allow_duplicates=True)
    cs_ws_data.insert(loc = 4, column = 'hits', value = demo_data['hits'], allow_duplicates=True)
    cs_ws_data.insert(loc = 5, column = 'miss', value = demo_data['miss'], allow_duplicates=True)
    cs_ws_data.insert(loc = 6, column = 'correct_source', value = demo_data['correct_source'], allow_duplicates=True)
    cs_ws_data.insert(loc = 7, column = 'wrong_source', value = demo_data['wrong_source'], allow_duplicates=True)
    cs_ws_data.insert(loc = 8, column = 'dprime', value = demo_data['dprime'], allow_duplicates=True)
    cs_ws_data.insert(loc = 9, column = 'associative_memScore', value = demo_data['associative_memScore'], allow_duplicates=True)    

    cs_ws_data.to_csv(os.path.join(output_dir, 'SVC_withinSub_cs_ws_'+str(numnet)+'networks.tsv'),
        sep='\t', header=True, index=False)


108391
training: 37 testing: 26
correctsource    25
wrongsource      12
Name: ctl_miss_ws_cs, dtype: int64 correctsource    18
wrongsource       8
Name: ctl_miss_ws_cs, dtype: int64
[0.66666667 0.5        0.66666667 0.16666667 0.6        0.75
 0.75      ]
Accuracy: 0.5675675675675675
               precision    recall  f1-score   support

correctsource       0.70      0.64      0.67        25
  wrongsource       0.36      0.42      0.38        12

    micro avg       0.57      0.57      0.57        37
    macro avg       0.53      0.53      0.53        37
 weighted avg       0.59      0.57      0.58        37

accuracy = 0.4230769230769231
               precision    recall  f1-score   support

correctsource       0.60      0.50      0.55        18
  wrongsource       0.18      0.25      0.21         8

    micro avg       0.42      0.42      0.42        26
    macro avg       0.39      0.38      0.38        26
 weighted avg       0.47      0.42      0.44        26

(7,)
[-0.49509168  

training: 39 testing: 27
correctsource    30
wrongsource       9
Name: ctl_miss_ws_cs, dtype: int64 correctsource    20
wrongsource       7
Name: ctl_miss_ws_cs, dtype: int64
[0.42857143 0.14285714 0.4        0.6        0.6        0.4
 0.2       ]
Accuracy: 0.38461538461538464
               precision    recall  f1-score   support

correctsource       0.64      0.47      0.54        30
  wrongsource       0.06      0.11      0.08         9

    micro avg       0.38      0.38      0.38        39
    macro avg       0.35      0.29      0.31        39
 weighted avg       0.50      0.38      0.43        39

accuracy = 0.48148148148148145
               precision    recall  f1-score   support

correctsource       0.75      0.45      0.56        20
  wrongsource       0.27      0.57      0.36         7

    micro avg       0.48      0.48      0.48        27
    macro avg       0.51      0.51      0.46        27
 weighted avg       0.62      0.48      0.51        27

(7,)
[-0.56009472 -0.0331

training: 30 testing: 21
wrongsource      16
correctsource    14
Name: ctl_miss_ws_cs, dtype: int64 wrongsource      11
correctsource    10
Name: ctl_miss_ws_cs, dtype: int64
[0.4  0.2  0.25 0.5  0.5  0.25 0.5 ]
Accuracy: 0.36666666666666664
               precision    recall  f1-score   support

correctsource       0.37      0.50      0.42        14
  wrongsource       0.36      0.25      0.30        16

    micro avg       0.37      0.37      0.37        30
    macro avg       0.37      0.38      0.36        30
 weighted avg       0.37      0.37      0.36        30

accuracy = 0.6666666666666666
               precision    recall  f1-score   support

correctsource       0.71      0.50      0.59        10
  wrongsource       0.64      0.82      0.72        11

    micro avg       0.67      0.67      0.67        21
    macro avg       0.68      0.66      0.65        21
 weighted avg       0.68      0.67      0.66        21

(7,)
[-0.67302953 -0.38984944 -0.80473366  0.33959127  0.09129

/anaconda3/envs/may19_py36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


training: 37 testing: 25
correctsource    21
wrongsource      16
Name: ctl_miss_ws_cs, dtype: int64 correctsource    15
wrongsource      10
Name: ctl_miss_ws_cs, dtype: int64
[0.33333333 0.33333333 0.2        0.4        0.4        0.4
 0.2       ]
Accuracy: 0.32432432432432434
               precision    recall  f1-score   support

correctsource       0.42      0.48      0.44        21
  wrongsource       0.15      0.12      0.14        16

    micro avg       0.32      0.32      0.32        37
    macro avg       0.29      0.30      0.29        37
 weighted avg       0.30      0.32      0.31        37

accuracy = 0.48
               precision    recall  f1-score   support

correctsource       0.60      0.40      0.48        15
  wrongsource       0.40      0.60      0.48        10

    micro avg       0.48      0.48      0.48        25
    macro avg       0.50      0.50      0.48        25
 weighted avg       0.52      0.48      0.48        25

(7,)
[ 0.25885923 -0.2245352  -0.0671215

...

training: 40 testing: 27
correctsource    23
wrongsource      17
Name: ctl_miss_ws_cs, dtype: int64 correctsource    15
wrongsource      12
Name: ctl_miss_ws_cs, dtype: int64
[0.42857143 0.71428571 0.16666667 0.8        0.8        0.6
 0.4       ]
Accuracy: 0.55
               precision    recall  f1-score   support

correctsource       0.61      0.61      0.61        23
  wrongsource       0.47      0.47      0.47        17

    micro avg       0.55      0.55      0.55        40
    macro avg       0.54      0.54      0.54        40
 weighted avg       0.55      0.55      0.55        40

accuracy = 0.6666666666666666
               precision    recall  f1-score   support

correctsource       0.67      0.80      0.73        15
  wrongsource       0.67      0.50      0.57        12

    micro avg       0.67      0.67      0.67        27
    macro avg       0.67      0.65      0.65        27
 weighted avg       0.67      0.67      0.66        27

(444,)
[ 0.00163759 -0.00966797 -0.016275

training: 43 testing: 30
correctsource    29
wrongsource      14
Name: ctl_miss_ws_cs, dtype: int64 correctsource    20
wrongsource      10
Name: ctl_miss_ws_cs, dtype: int64
[0.71428571 0.5        0.66666667 0.83333333 0.66666667 0.66666667
 0.66666667]
Accuracy: 0.6744186046511628
               precision    recall  f1-score   support

correctsource       0.76      0.76      0.76        29
  wrongsource       0.50      0.50      0.50        14

    micro avg       0.67      0.67      0.67        43
    macro avg       0.63      0.63      0.63        43
 weighted avg       0.67      0.67      0.67        43

accuracy = 0.4666666666666667
               precision    recall  f1-score   support

correctsource       0.61      0.55      0.58        20
  wrongsource       0.25      0.30      0.27        10

    micro avg       0.47      0.47      0.47        30
    macro avg       0.43      0.43      0.43        30
 weighted avg       0.49      0.47      0.48        30

(444,)
[ 2.83895124e

training: 46 testing: 31
correctsource    35
wrongsource      11
Name: ctl_miss_ws_cs, dtype: int64 correctsource    23
wrongsource       8
Name: ctl_miss_ws_cs, dtype: int64
[0.57142857 0.57142857 0.28571429 0.85714286 0.66666667 0.83333333
 0.66666667]
Accuracy: 0.6304347826086957
               precision    recall  f1-score   support

correctsource       0.74      0.80      0.77        35
  wrongsource       0.12      0.09      0.11        11

    micro avg       0.63      0.63      0.63        46
    macro avg       0.43      0.45      0.44        46
 weighted avg       0.59      0.63      0.61        46

accuracy = 0.7419354838709677
               precision    recall  f1-score   support

correctsource       0.76      0.96      0.85        23
  wrongsource       0.50      0.12      0.20         8

    micro avg       0.74      0.74      0.74        31
    macro avg       0.63      0.54      0.52        31
 weighted avg       0.69      0.74      0.68        31

(444,)
[-4.23335947e

training: 45 testing: 31
correctsource    36
wrongsource       9
Name: ctl_miss_ws_cs, dtype: int64 correctsource    25
wrongsource       6
Name: ctl_miss_ws_cs, dtype: int64
[0.875      0.57142857 0.5        0.66666667 1.         0.83333333
 0.33333333]
Accuracy: 0.6888888888888889
               precision    recall  f1-score   support

correctsource       0.81      0.81      0.81        36
  wrongsource       0.22      0.22      0.22         9

    micro avg       0.69      0.69      0.69        45
    macro avg       0.51      0.51      0.51        45
 weighted avg       0.69      0.69      0.69        45

accuracy = 0.6774193548387096
               precision    recall  f1-score   support

correctsource       0.78      0.84      0.81        25
  wrongsource       0.00      0.00      0.00         6

    micro avg       0.68      0.68      0.68        31
    macro avg       0.39      0.42      0.40        31
 weighted avg       0.63      0.68      0.65        31

(444,)
[ 1.83782589e

training: 40 testing: 27
correctsource    25
wrongsource      15
Name: ctl_miss_ws_cs, dtype: int64 correctsource    17
wrongsource      10
Name: ctl_miss_ws_cs, dtype: int64
[0.85714286 0.5        0.66666667 0.66666667 0.4        1.
 0.6       ]
Accuracy: 0.675
               precision    recall  f1-score   support

correctsource       0.77      0.68      0.72        25
  wrongsource       0.56      0.67      0.61        15

    micro avg       0.68      0.68      0.68        40
    macro avg       0.66      0.67      0.66        40
 weighted avg       0.69      0.68      0.68        40

accuracy = 0.37037037037037035
               precision    recall  f1-score   support

correctsource       0.50      0.47      0.48        17
  wrongsource       0.18      0.20      0.19        10

    micro avg       0.37      0.37      0.37        27
    macro avg       0.34      0.34      0.34        27
 weighted avg       0.38      0.37      0.38        27

(444,)
[ 1.12542511e-03 -3.45506178e-02 

In [11]:
# CORRECT SOURCE VERSUS MISSED TRIAL CLASSIFICATION

for numnet in numnets:
    
    basc = image.load_img(os.path.join(basc_dir, 'MIST_'+str(numnet)+'.nii'))
    b_labels = '/Users/mombot/Documents/Simexp/CIMAQ/Data/MIST/Release/Parcel_Information/MIST_'+str(numnet)+'.csv'
    basc_labels = pd.read_csv(b_labels, sep=';')

    # build data structure to store accuracy data and coefficients
    cs_miss_data = pd.DataFrame()
    cs_miss_data.insert(loc = 0, column = 'dccid', value = 'None', allow_duplicates=True)
    # cs_miss_data.insert(loc = 1, column = 'diagnosis', value = 'None', allow_duplicates=True)
    for i in range(0, 7):
        cs_miss_data.insert(loc = cs_miss_data.shape[1], column = 'CV'+str(i+1)+'_acc', value = NaN, allow_duplicates=True)
    cs_miss_data.insert(loc = cs_miss_data.shape[1], column = 'TrainSet_MeanCV_acc', value = 'None', allow_duplicates=True)
    cs_miss_data.insert(loc = cs_miss_data.shape[1], column = 'TestSet_acc', value = 'None', allow_duplicates=True)
    netnames = basc_labels['name']
    for i in range(0, numnet):
        cs_miss_data.insert(loc = cs_miss_data.shape[1], column = netnames[i]+'_coef', value = NaN, allow_duplicates=True)

    for sub in cmiss_subs:
        print(sub)
        s_data = [sub]
        # load subject's beta maps (one per trial)
        betas = image.load_img(img=os.path.join(beta_dir, str(sub), 'TrialContrasts/betas_sub'+str(sub)+'*.nii'),
                               wildcards=True)
        # initialize NiftiLabelMasker object    
        sub_mask = nb.load(os.path.join(mask_dir, 'func_sub'+str(sub)+'_mask_stereonl.nii'))
        sub_label_masker = NiftiLabelsMasker(labels_img=basc, standardize=True, mask_img=sub_mask,
                                             memory = 'nilearn_cache', verbose=0)

        # transform subject's beta maps into vector of network means per trial
        X_cs_ws_miss_ctl = sub_label_masker.fit_transform(betas)   

        # load subject's trial labels
        labels_file = os.path.join(label_dir, 'sub-'+str(sub)+'_ctl_miss_ws_cs.tsv')
        y_cs_ws_miss_ctl = pd.read_csv(labels_file, sep='\t')
        y_cs_ws_miss_ctl_labels = y_cs_ws_miss_ctl['ctl_miss_ws_cs']
        # mask X and y data to exclude trials of no interest
        cs_miss_mask = y_cs_ws_miss_ctl_labels.isin(['correctsource', 'missed'])
        y_cs_miss = y_cs_ws_miss_ctl_labels[cs_miss_mask]      
        X_cs_miss  = X_cs_ws_miss_ctl[cs_miss_mask]

        # Split trials into a training and a test set
        X_train, X_test, y_train, y_test = train_test_split(
            X_cs_miss, # x
            y_cs_miss, # y
            test_size = 0.4, # 60%/40% split
            shuffle = True, # shuffle dataset before splitting
            stratify = y_cs_miss, # keep distribution of conditions consistent betw. train & test sets
            #random_state = 123  # if set number, same shuffle each time, otherwise randomization algo
            ) 
        print('training:', len(X_train), 'testing:', len(X_test))
        print(y_train.value_counts(), y_test.value_counts())

        # define the model
        sub_svc = SVC(kernel='linear', class_weight='balanced')

        # do cross-validation to evaluate model performance
        # within 10 folds of training set
        # predict
        y_pred = cross_val_predict(sub_svc, X_train, y_train,
                                   groups=y_train, cv=7)
        # scores
        cv_acc = cross_val_score(sub_svc, X_train, y_train,
                             groups=y_train, cv=7)
        print(cv_acc)

        for i in range(0, len(cv_acc)):
            s_data.append(cv_acc[i])

        # evaluate overall model performance on training data
        overall_acc = accuracy_score(y_pred = y_pred, y_true = y_train)
        overall_cr = classification_report(y_pred = y_pred, y_true = y_train)
        print('Accuracy:',overall_acc)
        print(overall_cr)

        s_data.append(overall_acc)

        # Test model on unseen data from the test set
        sub_svc.fit(X_train, y_train)
        y_pred = sub_svc.predict(X_test) # classify age class using testing data
        acc = sub_svc.score(X_test, y_test) # get accuracy

        cr = classification_report(y_pred=y_pred, y_true=y_test) # get prec., recall & f1
        # print results
        print('accuracy =', acc)
        print(cr)  

        s_data.append(acc)

        # get coefficients
        coef_ = sub_svc.coef_[0]
        print(coef_.shape)
        print(coef_)

        sub_basc = basc_labels.copy()
        sub_basc.insert(loc=3, column='coef', value=coef_, allow_duplicates=True)

        coef = sub_basc['coef']
        for j in range(0, len(coef)):
            s_data.append(coef[j])

        #sub_basc.sort_values(by='coef', axis = 0, ascending = False, inplace=True)
        #print(sub_basc.iloc[0:12, 2:4])

        cs_miss_data = cs_miss_data.append(pd.Series(s_data, index=cs_miss_data.columns), ignore_index=True)

    demo_data = cmiss_data.copy()
    demo_data.reset_index(level=None, drop=False, inplace=True)

    cs_miss_data.insert(loc = 1, column = 'cognitive_status', value = demo_data['cognitive_status'], allow_duplicates=True)
    cs_miss_data.insert(loc = 2, column = 'total_scrubbed_frames', value = demo_data['total_scrubbed_frames'], allow_duplicates=True)
    cs_miss_data.insert(loc = 3, column = 'mean_FD', value = demo_data['mean_FD'], allow_duplicates=True)
    cs_miss_data.insert(loc = 4, column = 'hits', value = demo_data['hits'], allow_duplicates=True)
    cs_miss_data.insert(loc = 5, column = 'miss', value = demo_data['miss'], allow_duplicates=True)
    cs_miss_data.insert(loc = 6, column = 'correct_source', value = demo_data['correct_source'], allow_duplicates=True)
    cs_miss_data.insert(loc = 7, column = 'wrong_source', value = demo_data['wrong_source'], allow_duplicates=True)
    cs_miss_data.insert(loc = 8, column = 'dprime', value = demo_data['dprime'], allow_duplicates=True)
    cs_miss_data.insert(loc = 9, column = 'associative_memScore', value = demo_data['associative_memScore'], allow_duplicates=True)    

    cs_miss_data.to_csv(os.path.join(output_dir, 'SVC_withinSub_cs_miss_'+str(numnet)+'networks.tsv'),
        sep='\t', header=True, index=False)


108391
training: 34 testing: 24
correctsource    25
missed            9
Name: ctl_miss_ws_cs, dtype: int64 correctsource    18
missed            6
Name: ctl_miss_ws_cs, dtype: int64
[0.66666667 0.5        0.6        0.4        0.5        0.75
 0.5       ]
Accuracy: 0.5588235294117647
               precision    recall  f1-score   support

correctsource       0.81      0.52      0.63        25
       missed       0.33      0.67      0.44         9

    micro avg       0.56      0.56      0.56        34
    macro avg       0.57      0.59      0.54        34
 weighted avg       0.69      0.56      0.58        34

accuracy = 0.4166666666666667
               precision    recall  f1-score   support

correctsource       0.70      0.39      0.50        18
       missed       0.21      0.50      0.30         6

    micro avg       0.42      0.42      0.42        24
    macro avg       0.46      0.44      0.40        24
 weighted avg       0.58      0.42      0.45        24

(7,)
[-0.23810046  

training: 36 testing: 25
correctsource    22
missed           14
Name: ctl_miss_ws_cs, dtype: int64 correctsource    16
missed            9
Name: ctl_miss_ws_cs, dtype: int64
[0.66666667 0.6        0.6        0.4        0.6        0.6
 0.8       ]
Accuracy: 0.6111111111111112
               precision    recall  f1-score   support

correctsource       0.75      0.55      0.63        22
       missed       0.50      0.71      0.59        14

    micro avg       0.61      0.61      0.61        36
    macro avg       0.62      0.63      0.61        36
 weighted avg       0.65      0.61      0.61        36

accuracy = 0.68
               precision    recall  f1-score   support

correctsource       0.79      0.69      0.73        16
       missed       0.55      0.67      0.60         9

    micro avg       0.68      0.68      0.68        25
    macro avg       0.67      0.68      0.67        25
 weighted avg       0.70      0.68      0.69        25

(7,)
[ 0.62358384 -0.82972445 -0.68194531

training: 36 testing: 25
correctsource    22
missed           14
Name: ctl_miss_ws_cs, dtype: int64 correctsource    16
missed            9
Name: ctl_miss_ws_cs, dtype: int64
[0.33333333 0.6        0.4        0.4        0.6        0.4
 0.4       ]
Accuracy: 0.4444444444444444
               precision    recall  f1-score   support

correctsource       0.55      0.50      0.52        22
       missed       0.31      0.36      0.33        14

    micro avg       0.44      0.44      0.44        36
    macro avg       0.43      0.43      0.43        36
 weighted avg       0.46      0.44      0.45        36

accuracy = 0.52
               precision    recall  f1-score   support

correctsource       0.67      0.50      0.57        16
       missed       0.38      0.56      0.45         9

    micro avg       0.52      0.52      0.52        25
    macro avg       0.53      0.53      0.51        25
 weighted avg       0.57      0.52      0.53        25

(7,)
[ 0.53917801  0.05748084 -0.55365404

training: 34 testing: 23
missed           21
correctsource    13
Name: ctl_miss_ws_cs, dtype: int64 missed           15
correctsource     8
Name: ctl_miss_ws_cs, dtype: int64
[0.4  1.   0.8  0.6  0.6  0.6  0.25]
Accuracy: 0.6176470588235294
               precision    recall  f1-score   support

correctsource       0.50      0.69      0.58        13
       missed       0.75      0.57      0.65        21

    micro avg       0.62      0.62      0.62        34
    macro avg       0.62      0.63      0.61        34
 weighted avg       0.65      0.62      0.62        34

accuracy = 0.391304347826087
               precision    recall  f1-score   support

correctsource       0.12      0.12      0.12         8
       missed       0.53      0.53      0.53        15

    micro avg       0.39      0.39      0.39        23
    macro avg       0.33      0.33      0.33        23
 weighted avg       0.39      0.39      0.39        23

(7,)
[ 0.83891223 -0.2933732   0.52697091 -0.02304787  0.7181154

training: 32 testing: 22
correctsource    17
missed           15
Name: ctl_miss_ws_cs, dtype: int64 correctsource    12
missed           10
Name: ctl_miss_ws_cs, dtype: int64
[0.33333333 0.4        0.2        0.         0.5        0.5
 0.25      ]
Accuracy: 0.3125
               precision    recall  f1-score   support

correctsource       0.33      0.29      0.31        17
       missed       0.29      0.33      0.31        15

    micro avg       0.31      0.31      0.31        32
    macro avg       0.31      0.31      0.31        32
 weighted avg       0.31      0.31      0.31        32

accuracy = 0.45454545454545453
               precision    recall  f1-score   support

correctsource       0.50      0.42      0.45        12
       missed       0.42      0.50      0.45        10

    micro avg       0.45      0.45      0.45        22
    macro avg       0.46      0.46      0.45        22
 weighted avg       0.46      0.45      0.45        22

(7,)
[ 0.84794208  0.02318715  0.35861

...

training: 36 testing: 24
missed           26
correctsource    10
Name: ctl_miss_ws_cs, dtype: int64 missed           18
correctsource     6
Name: ctl_miss_ws_cs, dtype: int64
[0.66666667 0.66666667 0.66666667 0.6        0.4        0.5
 0.75      ]
Accuracy: 0.6111111111111112
               precision    recall  f1-score   support

correctsource       0.30      0.30      0.30        10
       missed       0.73      0.73      0.73        26

    micro avg       0.61      0.61      0.61        36
    macro avg       0.52      0.52      0.52        36
 weighted avg       0.61      0.61      0.61        36

accuracy = 0.5416666666666666
               precision    recall  f1-score   support

correctsource       0.27      0.50      0.35         6
       missed       0.77      0.56      0.65        18

    micro avg       0.54      0.54      0.54        24
    macro avg       0.52      0.53      0.50        24
 weighted avg       0.65      0.54      0.57        24

(444,)
[-0.00872425 -0.0134

training: 34 testing: 23
correctsource    24
missed           10
Name: ctl_miss_ws_cs, dtype: int64 correctsource    16
missed            7
Name: ctl_miss_ws_cs, dtype: int64
[0.66666667 0.5        0.5        0.5        0.5        0.5
 0.5       ]
Accuracy: 0.5294117647058824
               precision    recall  f1-score   support

correctsource       0.65      0.71      0.68        24
       missed       0.12      0.10      0.11        10

    micro avg       0.53      0.53      0.53        34
    macro avg       0.39      0.40      0.40        34
 weighted avg       0.50      0.53      0.51        34

accuracy = 0.6956521739130435
               precision    recall  f1-score   support

correctsource       0.74      0.88      0.80        16
       missed       0.50      0.29      0.36         7

    micro avg       0.70      0.70      0.70        23
    macro avg       0.62      0.58      0.58        23
 weighted avg       0.66      0.70      0.67        23

(444,)
[ 0.02339025  0.0225

training: 39 testing: 26
correctsource    27
missed           12
Name: ctl_miss_ws_cs, dtype: int64 correctsource    18
missed            8
Name: ctl_miss_ws_cs, dtype: int64
[0.5        0.5        0.66666667 0.83333333 0.83333333 0.6
 0.25      ]
Accuracy: 0.6153846153846154
               precision    recall  f1-score   support

correctsource       0.75      0.67      0.71        27
       missed       0.40      0.50      0.44        12

    micro avg       0.62      0.62      0.62        39
    macro avg       0.57      0.58      0.58        39
 weighted avg       0.64      0.62      0.63        39

accuracy = 0.5769230769230769
               precision    recall  f1-score   support

correctsource       0.71      0.67      0.69        18
       missed       0.33      0.38      0.35         8

    micro avg       0.58      0.58      0.58        26
    macro avg       0.52      0.52      0.52        26
 weighted avg       0.59      0.58      0.58        26

(444,)
[-0.00663641  0.0198

training: 38 testing: 26
missed           20
correctsource    18
Name: ctl_miss_ws_cs, dtype: int64 missed           13
correctsource    13
Name: ctl_miss_ws_cs, dtype: int64
[0.33333333 0.66666667 0.66666667 0.5        0.8        0.6
 1.        ]
Accuracy: 0.631578947368421
               precision    recall  f1-score   support

correctsource       0.62      0.56      0.59        18
       missed       0.64      0.70      0.67        20

    micro avg       0.63      0.63      0.63        38
    macro avg       0.63      0.63      0.63        38
 weighted avg       0.63      0.63      0.63        38

accuracy = 0.5
               precision    recall  f1-score   support

correctsource       0.50      0.23      0.32        13
       missed       0.50      0.77      0.61        13

    micro avg       0.50      0.50      0.50        26
    macro avg       0.50      0.50      0.46        26
 weighted avg       0.50      0.50      0.46        26

(444,)
[-1.29707726e-02  5.26494937e-03  3.

training: 37 testing: 26
correctsource    21
missed           16
Name: ctl_miss_ws_cs, dtype: int64 correctsource    14
missed           12
Name: ctl_miss_ws_cs, dtype: int64
[0.16666667 0.5        0.4        0.6        0.6        0.8
 0.6       ]
Accuracy: 0.5135135135135135
               precision    recall  f1-score   support

correctsource       0.56      0.67      0.61        21
       missed       0.42      0.31      0.36        16

    micro avg       0.51      0.51      0.51        37
    macro avg       0.49      0.49      0.48        37
 weighted avg       0.50      0.51      0.50        37

accuracy = 0.46153846153846156
               precision    recall  f1-score   support

correctsource       0.50      0.71      0.59        14
       missed       0.33      0.17      0.22        12

    micro avg       0.46      0.46      0.46        26
    macro avg       0.42      0.44      0.41        26
 weighted avg       0.42      0.46      0.42        26

(444,)
[ 1.70457095e-02  2